# Extract External catalogs

 work with Weakly_2024_07
- use jupyter kernel LSST
- author : Sylvie Dagoret-Campagne
- affiliation : IJCLab
- creation date : 2024/02/29
- update : 2024/03/04


Access to the external catalog

``quantum graphs ``: https://tigress-web.princeton.edu/~lkelvin/pipelines/w_2024_07/drp_pipe/LATISS/DRP/pipeline_drp_pipe_LATISS_DRP_step1.pdf

In [1]:
! eups list -s | grep LOCAL

analysis_tools        LOCAL:/home/d/dagoret/repos/repos_w_2024_07/analysis_tools 	setup
atmospec              LOCAL:/home/d/dagoret/repos/repos_w_2024_07/atmospec 	setup
eups                  LOCAL:/opt/lsst/software/stack/conda/miniconda3-py38_4.9.2/envs/lsst-scipipe-8.0.0/eups 	setup
spectractor           LOCAL:/home/d/dagoret/repos/repos_w_2024_07/Spectractor 	setup


In [2]:
! eups list -s lsst_distrib

   g4213664e8e+34187316c4 	current w_2024_07 setup


In [3]:
import lsst.daf.butler as dafButler
#import lsst.summit.utils.butlerUtils as butlerUtils

In [4]:
#import lsst.sphgeom
from  lsst.geom import SpherePoint, Angle

In [5]:
import astropy.coordinates as coord
import astropy.units as u
from astropy.time import Time
from astropy.coordinates import SkyCoord
from astropy import coordinates

In [6]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
from mpl_toolkits.axes_grid1 import make_axes_locatable
from matplotlib.colors import LogNorm,SymLogNorm


import matplotlib.ticker                         # here's where the formatter is
from matplotlib.ticker import (MultipleLocator, FormatStrFormatter,
                               AutoMinorLocator)

from astropy.visualization import (MinMaxInterval, SqrtStretch,ZScaleInterval,PercentileInterval,
                                   ImageNormalize,imshow_norm)
from astropy.visualization.stretch import SinhStretch, LinearStretch,AsinhStretch,LogStretch

from astropy.io import fits
from astropy.table import Table
import pandas as pd

import matplotlib.ticker                         # here's where the formatter is
import os
import re
import pandas as pd
import pickle

plt.rcParams["figure.figsize"] = (4,3)
plt.rcParams["axes.labelsize"] = 'xx-large'
plt.rcParams['axes.titlesize'] = 'xx-large'
plt.rcParams['xtick.labelsize']= 'xx-large'
plt.rcParams['ytick.labelsize']= 'xx-large'

In [7]:
from matplotlib.ticker import (MultipleLocator, FormatStrFormatter,
                               AutoMinorLocator)

from astropy.visualization import (MinMaxInterval, SqrtStretch,ZScaleInterval,PercentileInterval,
                                   ImageNormalize,imshow_norm)
from astropy.visualization.stretch import SinhStretch, LinearStretch,AsinhStretch,LogStretch

from astropy.time import Time


In [8]:
# LSST Display
import lsst.afw.display as afwDisplay
afwDisplay.setDefaultBackend('matplotlib')

In [9]:
transform = AsinhStretch() + PercentileInterval(99.)

In [10]:
pd.options.display.max_columns = None
#pd.options.display.max_rows = None

## Configuration

In [11]:
DATE = 202402
#filesource_out="finalized_src_table_202402.csv"
#filetractpatch_out = 'Latiss_tractspatchs_202312.pickle'

In [12]:
#repo =  "/sdf/group/rubin/repo/main"
repo = "/sdf/group/rubin/repo/oga/"
butler = dafButler.Butler(repo)
registry = butler.registry
skymap_auxtel ='latiss_v1'

In [13]:
#file_out="sourceTable_202312.csv"

## Give the collection

In [14]:
#my_collection = "LATISS/runs/AUXTEL_DRP_IMAGING_2023-11A-10A-09AB-08ABC-07AB-05AB/w_2023_46/PREOPS-4553"
my_collection = "LATISS/runs/AUXTEL_DRP_IMAGING_20230509_20240201/w_2024_05/PREOPS-4871"

## Config

# Tracts and Patches

In [15]:
skymap = butler.get('skyMap', skymap=skymap_auxtel, collections=my_collection)

In [16]:
# Load data (deserialize)
import pickle
#with open('Latiss_tractspatchs.pickle', 'rb') as handle:
with open('../data/202402/Latiss_tractspatchs_radec_htm7_skypixels_202402.pickle', 'rb') as handle:
    tracts_patchs_dict = pickle.load(handle)

In [17]:
tracts_patchs_dict

{382: {'htmpixels': array([135892, 135895]),
  'radec': array([ 11.83559184,  12.69437584, -72.91970512, -72.82704592])},
 383: {'htmpixels': array([135892, 135895]),
  'radec': array([ 12.30552976,  12.88215539, -72.91694386, -72.82704468])},
 452: {'htmpixels': array([135696, 135699]),
  'radec': array([  0.69689026,   1.83680741, -72.85580215, -72.60316762])},
 455: {'htmpixels': array([135892, 135894, 135895]),
  'radec': array([ 12.00059065,  12.86592199, -72.93792989, -72.68219831])},
 3863: {'htmpixels': array([162489, 162491]),
  'radec': array([119.93688346, 120.2482689 , -36.32070757, -36.06942145])},
 3864: {'htmpixels': array([162888, 162891]),
  'radec': array([122.28140604, 122.69508293, -36.32124229, -35.98768246])},
 5614: {'htmpixels': array([177672, 177716]),
  'radec': array([238.7893974 , 239.15622802, -24.41986978, -24.16893036])},
 5615: {'htmpixels': array([177675]),
  'radec': array([239.8629916 , 240.13697795, -24.17042533, -23.83709706])},
 5616: {'htmpixels':

In [18]:
all_skypixels = []
for key, value in tracts_patchs_dict.items():
    all_skypixels.append(value['htmpixels'])
all_skypixels = np.concatenate(all_skypixels)
all_sypixels= np.unique(all_skypixels)
all_skypixels = np.sort(all_skypixels)
all_skypixels  
NPIX = len(all_skypixels)

# Reference Sources

## Dump

In [19]:
catList = list(butler.registry.queryDatasetTypes('*refc*'))
# Note: please ignore the Spectractor WARNING messages below, they are to be expected here.

In [20]:
for cat in catList:
    print("-------------------------------------------------------------------")
    print(cat)

-------------------------------------------------------------------
DatasetType('atlas_refcat2_20220201', {htm7}, SimpleCatalog)
-------------------------------------------------------------------
DatasetType('isolated_star_sources_atlas_refcat2_20220201_match', {skymap, tract}, DataFrame)
-------------------------------------------------------------------
DatasetType('sourceTable_visit_atlas_refcat2_20220201_match', {band, instrument, physical_filter, visit}, DataFrame)
-------------------------------------------------------------------
DatasetType('objectTable_tract_atlas_refcat2_20220201_match', {skymap, tract}, ArrowAstropy)
-------------------------------------------------------------------
DatasetType('objectTable_tract_atlas_refcat2_20220201_match_g_targetRefCatDeltaPsfSkyPlot_SkyPlot', {skymap, tract}, Plot)
-------------------------------------------------------------------
DatasetType('objectTable_tract_atlas_refcat2_20220201_match_y_targetRefCatDeltaPsfSkyPlot_SkyPlot', {sky

In [21]:
mycat = 'atlas_refcat2_20220201'

In [22]:
#data_product = "gaia_dr2_20200414" 
#data_product = "gaia_dr3_20230707"
data_product = 'atlas_refcat2_20220201'

datasetRefs = butler.registry.queryDatasets(datasetType=data_product, collections=my_collection, where= "instrument='LATISS'")
filesource_out=f"{data_product}_{DATE}.csv"

for i, ref in enumerate(datasetRefs):
    print(f"========================datasetType = {data_product} ============================================")
    print("fullId.............................:",ref.dataId.full)
    if i >0:
        break

========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 131072}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 131073}


/tmp/ipykernel_12097/4204358590.py:10: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId.............................:",ref.dataId.full)


In [23]:
registry.getDatasetType(data_product)

DatasetType('atlas_refcat2_20220201', {htm7}, SimpleCatalog)

In [24]:
print(butler.registry.dimensions['htm7'].RecordClass.fields)

htm7: 
  id: int
  region: lsst.sphgeom.Region


In [25]:
for tractID in tracts_patchs_dict.keys():
    List_of_Skypixels = tracts_patchs_dict[tractID]['htmpixels']
    print(tractID,  List_of_Skypixels)
    for htm7_id in List_of_Skypixels:
        where_clause = f"instrument='LATISS' AND detector=0 AND htm7={htm7_id}"
        #where_clause = f"instrument='LATISS' AND detector=0"
        dataId = {'htm7': htm7_id}
        print("ask for where and dataId : ",where_clause,dataId)
        datasetRefs = butler.registry.queryDatasets(datasetType=data_product,  dataId=dataId,collections=my_collection,where=where_clause)
        #datasetRefs = registry.queryDatasets(data_product, dataId=dataId)
        print("fullId.............................:",ref.dataId.full)

382 [135892 135895]
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=135892 {'htm7': 135892}
fullId.............................: {htm7: 131073}
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=135895 {'htm7': 135895}
fullId.............................: {htm7: 131073}
383 [135892 135895]
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=135892 {'htm7': 135892}
fullId.............................: {htm7: 131073}
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=135895 {'htm7': 135895}
fullId.............................: {htm7: 131073}
452 [135696 135699]
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=135696 {'htm7': 135696}
fullId.............................: {htm7: 131073}
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=135699 {'htm7': 135699}
fullId.............................: {htm7: 131073}
455 [135892 135894 135895]
ask for where and dataId 

/tmp/ipykernel_12097/307131730.py:11: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId.............................:",ref.dataId.full)


fullId.............................: {htm7: 131073}
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=135895 {'htm7': 135895}
fullId.............................: {htm7: 131073}
3863 [162489 162491]
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=162489 {'htm7': 162489}
fullId.............................: {htm7: 131073}
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=162491 {'htm7': 162491}
fullId.............................: {htm7: 131073}
3864 [162888 162891]
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=162888 {'htm7': 162888}
fullId.............................: {htm7: 131073}
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=162891 {'htm7': 162891}
fullId.............................: {htm7: 131073}
5614 [177672 177716]
ask for where and dataId :  instrument='LATISS' AND detector=0 AND htm7=177672 {'htm7': 177672}
fullId.............................: {htm7: 13107

In [26]:
datasetRefs = butler.registry.queryDatasets(datasetType=data_product, collections=my_collection, where= "instrument='LATISS'")

In [27]:
all_df = []

count = 0
for i, ref in enumerate(datasetRefs):
    print(f"========================datasetType = {data_product} ============================================")
    print("fullId.............................:",ref.dataId.full)
  
    skypix = ref.dataId['htm7']
    if skypix not in all_skypixels:
        continue

    if count> NPIX:
        break
        
    t = butler.get(ref).asAstropy()
    df = t.to_pandas()
    #df.rename(columns={"coord_ra": "ra", "coord_dec": "dec"}, errors="raise",inplace=True)
    #df[["tractID","patchID"]] = df.apply( FindTractAndPatch, axis=1,result_type ='expand')
    #if(len(df)>0):
    #print(type(df),len(df))
    df['skypix'] = skypix
    all_df.append(df)
    count += 1

 
    

========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 131072}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 131073}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 131074}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 131075}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 131076}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 131077}
========================datasetType = atlas_refcat2_

/tmp/ipykernel_12097/3723741279.py:6: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId.............................:",ref.dataId.full)


========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 134482}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 134596}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 134483}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 134315}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 134597}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 134316}
========================datasetType = atlas_refcat2_

/tmp/ipykernel_12097/3723741279.py:6: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId.............................:",ref.dataId.full)
/tmp/ipykernel_12097/3723741279.py:6: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId.............................:",ref.dataId.full)


========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 136030}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 136213}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 135893}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 136214}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 136031}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 135894}


...

/tmp/ipykernel_12097/3723741279.py:6: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId.............................:",ref.dataId.full)
/tmp/ipykernel_12097/3723741279.py:6: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId.............................:",ref.dataId.full)


========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 182080}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 181581}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 182081}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 182011}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 181582}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 182012}
========================datasetType = atlas_refcat2_

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 221139}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 221140}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 221494}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 221495}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 221496}
========================datasetType = atlas_refcat2_20220201 ============================================
fullId.............................: {htm7: 221497}
========================datasetType = atlas_refcat2_

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [28]:
df.columns

Index(['id', 'coord_ra', 'coord_dec', 'g_flux', 'r_flux', 'i_flux', 'z_flux',
       'g_fluxErr', 'r_fluxErr', 'i_fluxErr', 'z_fluxErr', 'variable', 'epoch',
       'pm_ra', 'pm_dec', 'pm_raErr', 'pm_decErr', 'pm_flag', 'parallax',
       'parallaxErr', 'parallax_flag', 'Ag', 'skypix'],
      dtype='object')

In [29]:
df = pd.concat(all_df)

In [30]:
df

id  coord_ra  coord_dec         g_flux         r_flux  \
0      20250001146157390  0.002000  -1.276166   10452.024041   50396.502778   
1      20250001184196331  0.002067  -1.276181   13601.913229   41114.972110   
2      20250003818199141  0.006664  -1.276140   81432.993523  117597.909095   
3      20260000854748562  0.001492  -1.276003    7112.135137   30422.885295   
4      20260001535944702  0.002681  -1.276059  188104.679641  360080.497527   
...                  ...       ...        ...            ...            ...   
5691  116233079445224336  5.374646   0.119757   32960.971218   56078.966337   
5692  116233079495266290  5.374733   0.119785  386901.131655  946238.032883   
5693  116233079506521351  5.374753   0.119713   33542.853083   89701.560841   
5694  116233079525239419  5.374785   0.119831   19444.662074   64744.070457   
5695  116233079632993288  5.374974   0.119742   44340.399324  138420.240667   

            i_flux        z_flux    g_fluxErr     r_fluxErr     i_fluxErr  \
0     1.302566e+05  2.165707e+05  1819.550582   5895.301894  12357.731463   
1     7.585769e+04  1.037527e+05  1929.401669   4468.728156   7406.403935   
2     1.328007e+05  1.402167e+05  8325.787224  11265.095252  12476.779522   
3     7.211081e+04  1.140775e+05  1428.099288   3839.042009   6907.734996   
4     4.246196e+05  4.504013e+05  8143.280009  14924.990454   8995.592319   
...            ...           ...          ...           ...           ...   
5691  6.963064e+04  7.733919e+04  3643.201357   5475.298416   6670.151040   
5692  1.475027e+06  1.829785e+06  3920.077148   8715.700946  13586.322531   
5693  1.411238e+05  1.747429e+05   741.503441   1074.101397   1429.864929   
5694  1.953440e+05  3.293060e+05   483.577526    954.161609   1979.222476   
5695  3.548134e+05  5.410039e+05   571.780796   1402.472047   3268.149540   

         z_fluxErr  variable         epoch         pm_ra        pm_dec  \
0     20546.542634      True  57205.873819  1.082104e-07 -1.856836e-08   
1     10129.952157      True  57205.873819  6.108652e-08 -4.246968e-08   
2     13173.515923      True  57205.873819  3.160985e-08  4.605730e-09   
3     11032.939279      True  57205.873819  7.121913e-08  1.619278e-08   
4     17838.979015      True  57205.873819 -1.978040e-08 -2.933123e-08   
...            ...       ...           ...           ...           ...   
5691   7408.578181      True  57205.873819 -1.658063e-08 -1.546556e-08   
5692  16853.958502      True  57205.873819  3.388848e-08 -8.290314e-09   
5693   2253.354728      True  57205.873819 -3.364607e-08 -3.102808e-09   
5694   3639.844037      True  57205.873819  8.484239e-09 -5.250532e-08   
5695   6478.070667      True  57205.873819 -2.433765e-08 -4.891770e-08   

          pm_raErr     pm_decErr  pm_flag      parallax   parallaxErr  \
0     3.345214e-09  2.278624e-09    False  8.484239e-09  1.454441e-09   
1     4.363323e-09  3.054326e-09    False  5.720801e-09  1.939255e-09   
2     2.230143e-09  1.405960e-09    False  5.332950e-10  9.211460e-10   
3     4.848137e-09  3.345214e-09    False  3.199770e-09  2.181662e-09   
4     1.066590e-09  7.272206e-10    False  2.375587e-09  4.848137e-10   
...            ...           ...      ...           ...           ...   
5691  3.005845e-09  2.617994e-09    False  3.151289e-09  1.842292e-09   
5692  4.363323e-10  3.393696e-10    False  5.720801e-09  2.908882e-10   
5693  2.181662e-09  1.939255e-09    False  1.599885e-09  1.308997e-09   
5694  1.890773e-09  1.648367e-09    False  6.254096e-09  1.163553e-09   
5695  1.212034e-09  1.163553e-09    False  8.581202e-09  7.272206e-10   

      parallax_flag     Ag  skypix  
0             False  0.105  135696  
1             False  0.107  135696  
2             False  0.107  135696  
3             False  0.106  135696  
4             False  0.110  135696  
...             ...    ...     ...  
5691          False  0.288  205936  
5692          False  0.283  205936  
5693          False  0.282  205936  
5694        

In [31]:
df.to_csv(filesource_out)

In [32]:
print(df.columns.tolist())

['id', 'coord_ra', 'coord_dec', 'g_flux', 'r_flux', 'i_flux', 'z_flux', 'g_fluxErr', 'r_fluxErr', 'i_fluxErr', 'z_fluxErr', 'variable', 'epoch', 'pm_ra', 'pm_dec', 'pm_raErr', 'pm_decErr', 'pm_flag', 'parallax', 'parallaxErr', 'parallax_flag', 'Ag', 'skypix']
